In [0]:
# Read as Spark DataFrame
df = spark.table("workspace.default.business_financial_data_june_2025_quarter")

# Show first few rows
display(df)


Series_reference Period Data_value Suppressed STATUS UNITS Magnitude Subject Group Series_title_1 Series_title_2 Series_title_3 Series_title_4 Series_title_5 BDCQ.SF1AA2CA 2016.06 1116.386 null F Dollars 6 Business Data Collection - BDC Industry by financial variable (NZSIOC Level 2) Sales (operating income) Forestry and Logging Current prices Unadjusted null BDCQ.SF1AA2CA 2016.09 1070.874 null F Dollars 6 Business Data Collection - BDC Industry by financial variable (NZSIOC Level 2) Sales (operating income) Forestry and Logging Current prices Unadjusted null BDCQ.SF1AA2CA 2016.12 1054.408 null F Dollars 6 Business Data Collection - BDC Industry by financial variable (NZSIOC Level 2) Sales (operating income) Forestry and Logging Current prices Unadjusted null BDCQ.SF1AA2CA 2017.03 1010.665 null F Dollars 6 Business Data Collection - BDC Industry by financial variable (NZSIOC Level 2) Sales (operating income) Forestry and Logging Current prices Unadjusted null BDCQ.SF1AA2CA 2017.06 1233.7 null F Dollars 6 Business Data Collection - BDC Industry by financial variable (NZSIOC Level 2) Sales (operating income) Forestry and Logging Current prices Unadjusted null BDCQ.SF1AA2CA 2017.09 1282.436 null F Dollars 6 Business Data Collection - BDC Industry by financial variable (NZSIOC Level 2) Sales (operating income) Forestry and Logging Current prices Unadjusted null BDCQ.SF1AA2CA 2017.12 1290.82 null F Dollars 6 Business Data Collection - BDC Industry by financial variable (NZSIOC Level 2) Sales (operating income) Forestry and Logging Current prices Unadjusted null BDCQ.SF1AA2CA 2018.03 1412.007 null F Dollars 6 Business Data Collection - BDC Industry by financial variable (NZSIOC Level 2) Sales (operating income) Forestry and Logging Current prices Unadjusted null BDCQ.SF1AA2CA 2018.06 1488.055 null F Dollars 6 Business Data Collection - BDC Industry by financial variable (NZSIOC Level 2) Sales (operating income) Forestry and Logging Current prices Unadjusted null BDCQ.SF1AA2CA 2018.09 1497.678 null F Dollars 6 Business Data Collection - BDC Industry by financial variable (NZSIOC Level 2) Sales (operating income) Forestry and Logging Current prices Unadjusted null BDCQ.SF1AA2CA 2018.12 1570.507 null F Dollars 6 Business Data Collection - BDC Industry by financial variable (NZSIOC Level 2) Sales (operating income) Forestry and Logging Current prices Unadjusted null BDCQ.SF1AA2CA 2019.03 1393.749 null F Dollars 6 Business Data Collection - BDC Industry by financial variable (NZSIOC Level 2) Sales (operating income) Forestry and Logging Current prices Unadjusted null BDCQ.SF1AA2CA 2019.06 1517.143 null F Dollars 6 Business Data Collection - BDC Industry by financial variable (NZSIOC Level 2) Sales (operating income) Forestry and Logging Current prices Unadjusted null BDCQ.SF1AA2CA 2019.09 1381.514 null F Dollars 6 Business Data Collection - BDC Industry by financial variable (NZSIOC Level 2) Sales (operating income) Forestry and Logging Current prices Unadjusted null BDCQ.SF1AA2CA 2019.12 1370.985 null F Dollars 6 Business Data Collection - BDC Industry by financial variable (NZSIOC Level 2) Sales (operating income) Forestry and Logging Current prices Unadjusted null BDCQ.SF1AA2CA 2020.03 1073.017 null F Dollars 6 Business Data Collection - BDC Industry by financial variable (NZSIOC Level 2) Sales (operating income) Forestry and Logging Current prices Unadjusted null BDCQ.SF1AA2CA 2020.06 1131.445 null F Dollars 6 Business Data Collection - BDC Industry by financial variable (NZSIOC Level 2) Sales (operating income) Forestry and Logging Current prices Unadjusted null BDCQ.SF1AA2CA 2020.09 1440.101 null F Dollars 6 Business Data Collection - BDC Industry by financial variable (NZSIOC Level 2) Sales (operating income) Forestry and Logging Current prices Unadjusted null BDCQ.SF1AA2CA 2020.12 1489.979 null F Dollars 6 Business Data Collection - BDC Industry by financial variable (NZSIOC Level 2) Sales (operating income) Forestry and Logging 

Databricks visualization. Run in Databricks to view.

In [0]:
%sql
CREATE OR REPLACE TABLE raw_financial_data AS
SELECT *
FROM workspace.default.business_financial_data_june_2025_quarter;


num_affected_rows num_inserted_rows

In [0]:
%sql
CREATE OR REPLACE TABLE cleaned_financial_data AS
SELECT 
    Series_reference,
    CAST(Period AS STRING) AS Period,          -- Keep period as YYYY.MM
    CAST(Data_value AS DOUBLE) AS Data_value,  -- Convert to numeric
    STATUS,
    UNITS,
    Subject,
    `Group`,
    Series_title_1,
    Series_title_2,
    Series_title_3
FROM raw_financial_data
WHERE Data_value IS NOT NULL;


num_affected_rows num_inserted_rows

In [0]:
%sql
CREATE OR REPLACE TABLE transformed_financial_data AS
SELECT
    Series_reference,
    SPLIT(Period, '\\.')[0] AS Year,                      -- extract year
    CASE SPLIT(Period, '\\.')[1]
        WHEN '03' THEN 'Q1'
        WHEN '06' THEN 'Q2'
        WHEN '09' THEN 'Q3'
        WHEN '12' THEN 'Q4'
    END AS Quarter,                                       -- derive quarter
    Data_value,
    STATUS,
    UNITS,
    Subject,
    Series_title_1,
    Series_title_2,
    Series_title_3
FROM cleaned_financial_data;


num_affected_rows num_inserted_rows

Databricks visualization. Run in Databricks to view.

In [0]:
%sql
-- Quarterly summary
CREATE OR REPLACE TABLE quarterly_sales_summary AS
SELECT 
    Year,
    Quarter,
    SUM(Data_value) AS Total_Sales
FROM transformed_financial_data
GROUP BY Year, Quarter
ORDER BY Year, Quarter;

-- Yearly summary
CREATE OR REPLACE TABLE yearly_sales_summary AS
SELECT 
    Year,
    SUM(Data_value) AS Yearly_Sales
FROM transformed_financial_data
GROUP BY Year
ORDER BY Year;


num_affected_rows num_inserted_rows

In [0]:
%sql
CREATE OR REPLACE TABLE final_sales_analysis AS
SELECT 
    t.Year,
    t.Quarter,
    t.Series_reference,
    t.Data_value,
    y.Yearly_Sales,
    q.Total_Sales AS Quarterly_Sales
FROM transformed_financial_data t
LEFT JOIN yearly_sales_summary y ON t.Year = y.Year
LEFT JOIN quarterly_sales_summary q ON t.Year = q.Year AND t.Quarter = q.Quarter;


num_affected_rows num_inserted_rows